# COVID-19 Modeling

This notebook runs our revised Susceptible - Infected - Removed (SIR) model to look at several scenarios for the COVID-19 Pandemic.

## System and Python Module Requirements

* Python 3, running on Linux, macOS, or Windows
* `bokeh`, an interactive Python plotting module
* `numpy`
* `scipy`, a Python module for doing complex mathematics and scientific operations
* `ipywidgets`, which bring user-interactive widgets to Jupyter Notebooks

To install the Python modules, open a Terminal, Command Prompt, or Windows PowerShell and run the following command for each module that is not currently installed on your machine (bokeh, numpy, scipy, and ipywidgets). If you run into any issues with permissions while installing the modules, run the command as a superuser (`sudo pip3 install ...`) on macOS/Linux or administrator on Windows, or install the modules in a virtual environment.

```
pip3 install name_of_module_goes_here
```
**Note:** The `ipywidgets` module needs to be activated with the following command. I recommend you run the command in a second Terminal window after starting the Jupyter notebook.

```
jupyter nbextension enable --py widgetsnbextension
```

**You will need to run this command every time you start the Jupyter Notebook kernel.** The kernel starts when you run the `jupyter notebook` command.

### Browser Requirements

The Jupyter notebook will run in any browser, but some of the calendar dates may not work in Safari. I recommend running this notebook in Google Chrome.

## The Susceptible - Infected - Removed (SIR) Model

The SIR model is a simple epidemiological model that calculates the number of people infected with a contagious illness over a period of time. The model consists of a system of three differential equations that calculate the following parameters:

* **S**: The number of susceptible people
* **I**: The number of infected people
* **R**: The number of "removed" people, who are either recovered, dead, or immune.

Other variables in the model include:

* **Beta**: controls how often a susceptible-infected contact results in a new infection
* **Gamma**: The rate an infected person recovers and moves into the resistant phase
* **N**: The population
* **R0**: the reproduction number (called R naught), which is the average number of susceptible people to which an infected person spreads the disease over the course of their illness.
* **f**: Ther percentage of the population observing social distancing (experimental).

#### Instructions to Run the Model

1. Run the block of code below. It should automatically scroll down to the user interface below it.
2. Click on the tab you wish to plot with the model. The model outputs published on my COVID-19 Tracker application use the "Multiple RNaughts" tab.
3. Set the parameters. Please note that there is a lot of data being loaded when you change the parameters, so please be patient while the data loads.
4. Click on the "Plot Data" button.

#### Experimental Social Distancing Parameters
We are working on adding a parameter to the model to identify the percentage of the population that is practicing social distancing. Those outputs are currently considered experimental, and I make no guarantees that those outputs are accurate.

#### Interactive Model Output Plots
Because this notebook uses the `bokeh` module to display the model outputs, the plots are fully interactive, so you can zoom, pan, click, and even save the plot to a \*.png file.

In [2]:
import math
import datetime
import csv
import os
import itertools
import urllib.request
import json
import numpy as np
import ipywidgets as widgets
import matplotlib
import matplotlib.pyplot as plt
import matplotlib.dates as mdates
from matplotlib.offsetbox import AnchoredText
from IPython.display import display, clear_output
from bokeh.io import output_notebook
from bokeh.plotting import figure, show
from bokeh.models import Span
from bokeh.models.annotations import Title
from bokeh.palettes import Dark2_5 as palette
from scipy.integrate import odeint


class Segment(object):
    """ Defines a one-day segment of a curve for best-fitting the
    model data to the actual data.
    
    Note: The rnaught and self.r0 parameters are currently not
    being used.
    
    :param Tmin: The number of cases at the beginning of the day
    :type Tmin: int
    :param Tmax: The number of cases at the end of the day
    :type Tmax: int
    """
    
    def __init__(self, Tmin, Tmax, rnaught=None):
        self.T_min = Tmin
        self.T_max = Tmax
        self.r0 = rnaught
    
    @property
    def slope(self):
        return self.T_max - self.T_min


class SegmentDelta(object):
    """ Compares the one day segment for the model vs the actual data
    
    :param actual_segment: A Segment object containing data from the
    actual/observed data
    :type actual_segment: :class: `Segment`
    :param model_segment: A Segment object containing data from the
    model output data
    :type actual_segment: :class: `Segment`
    """
    
    def __init__(self, actual_segment, model_segment):
        self.actual_segment = actual_segment
        self.model_segment = model_segment
    
    @property
    def T_min(self):
        return abs(self.actual_segment.T_min - self.model_segment.T_min)
    
    @property
    def T_max(self):
        return abs(self.actual_segment.T_max - self.model_segment.T_max)
    
    @property
    def slope(self):
        return abs(self.actual_segment.slope - self.model_segment.slope)


class ClosestHits(object):
    """ Stores the closest matches between the model and actual data
    for best-fitting the model data to actual data.
    
    :param length_t: The number of days in the model/observations,
    whichever one is shorter.
    :type length_t: int
    """
    
    def __init__(self, length_t):
        self.T_min = [1e100 for x in range(length_t)]
        self.T_max = [1e100 for x in range(length_t)]
        self.slope = [1e100 for x in range(length_t)]

        
class BestFitOutput(object):
    """ Stores the best fit R Naught and Percent of the Population
    that gets infected between the model and actual data for 
    best-fitting the model data to actual data.
    
    :param length_t: The number of days in the model/observations,
    whichever one is shorter.
    :type length_t: int
    """
    
    def __init__(self, length_t):
        self.rnaughts = [-9999 for x in range(length_t)]
        self.percents_infected = [-9999 for x in range(length_t)]
    
    @property
    def avg_rnaught(self):
        return round(sum(self.rnaughts[-10:]) / len(self.rnaughts[-10:]), 1)
    
    @property
    def latest_rnaught(self):
        return self.rnaughts[-1]
    
    @property
    def avg_percent_infected(self):
        return round(sum(self.percents_infected[-10:]) / len(self.percents_infected[-10:]), 2)
    
    @property
    def latest_percent_infected(self):
        return self.percents_infected[-1]
    

def sir_model(y, t, N, beta, gamma, f=0):
    """ Defines and returns the system of three differential equations
    that define the SIR model.
    
    :param y: The susceptible/infected/removed parameters, which are plotted on the y-axis
    :type y: tuple
    :param t: The time steps, which are plotted on the x-axis. Can be a list of integers or `datetime` objects.
    :type t: list
    :param N: The total population of the entity (city/state/country) being modeled
    :type N: int
    :param beta: Number of contacts per day that are sufficient to spread the disease
    :type beta: float
    :param gamma: The rate an infected person recovers and moves into the resistant phase, in units of 1/days
    :type gamma: float
    :param f: The percent of the population complying with social distancing (0 to 100)
    :type f: float
    
    :return: The system of differential equations dS/dt, dI/dt, and dR/dt
    :rtype: tuple
    """
    f = f/100
    S, I, R = y
    dSdt = (-beta * S * I * (1 - f)**2) / N
    dIdt = (beta * S * I * (1 - f)**2) / N - gamma * I
    dRdt = gamma * I
    return dSdt, dIdt, dRdt


def x_axis_dates(t, day100):
    """Converts the x-axis from a list of days since the 100th case to a list of calendar days
    
    :param t: Array of days since the 100th case (integers)
    :type t: :class: `numpy.ndarray`
    :param day100: The calendar date that the 100th case was observed
    :type day100: :class: `datetime.datetime`
    
    :return: A numpy array of calendar dates that the model was run for
    :rtype: :class: `numpy.ndarray`
    """
    t_dates = [day100 + datetime.timedelta(days=int(x)) for x in t]
    t_dates = np.asarray(t_dates)
    return t_dates


def entity_name():
    """ Generate the name of the location being modeled, which is put on the title of the plot.
    These names are based on the dropdown menus selected, and will be in one of the following formats:
        * City                           * State
        * City, State                    * State, Country
        * City, Country                  * Country
        * City, State, Country
    
    :return: The name of the location, in one of the formats listed above
    :rtype: str
    """
    name_string = ""
    # City
    if int(city_selector.value) > 0:
        entity_obj = city_selector
        for t in entity_obj.options:
            if t[1] == entity_obj.value:
                name_string += t[0]
                break
    # State
    if int(state_selector.value) > 0:
        entity_obj = state_selector
        for t in entity_obj.options:
            if t[1] == entity_obj.value:
                if name_string != "":
                    name_string += ", "
                name_string += t[0]
                break
    # Country
    if int(country_selector.value) > 0:
        entity_obj = country_selector
        for t in entity_obj.options:
            if t[1] == entity_obj.value:
                if name_string != "":
                    name_string += ", "
                name_string += t[0]
                break
    return name_string


def get_actual_data():
    """ Loads the actual/observed state/country data into a numpy array
    
    :return: A numpy array containing the actual/observed number of cases
    each day.
    :rtype: :class: `numpy.nparray`
    """
    if int(city_selector.value) > 0:
        actual_data = []
    elif int(state_selector.value) > 0:
        if yaxis_selector.value in ["new", "riskindex"]:
            actual_data = ACTUAL_STATE_DATA[state_selector.value]['new_cases']
            actual_data = moving_average(actual_data)
            if yaxis_selector.value == "riskindex":
                actual_data = new_cases_to_risk_index(actual_data)
        else:
            actual_data = ACTUAL_STATE_DATA[state_selector.value]['confirmed']
    elif int(country_selector.value) > 0:
        if yaxis_selector.value in ["new", "riskindex"]:
            actual_data = ACTUAL_COUNTRY_DATA[country_selector.value]['new_cases']
            actual_data = moving_average(actual_data)
            if yaxis_selector.value == "riskindex":
                actual_data = new_cases_to_risk_index(actual_data)
        else:
            actual_data = ACTUAL_COUNTRY_DATA[country_selector.value]['confirmed']
    actual_data = [int(x) for x in actual_data]
    actual_data = np.asarray(actual_data)
    return actual_data


def moving_average(y_array, num_days=7):
    """ Calculates the moving average over an array
    
    :param y_array: A list of y-axis values (new cases/deaths)
    :type y_array: list
    :param num_days: The number of days over which to calculate the moving average
    :type num_days: int
    
    :return: The moving average y-axis data
    :rtype: list
    """
    data_moving_avg = []
    for i in range(len(y_array)):
        end_index = 1 if i == 0 else i + 1
        start_index = i - (num_days - 1)
        if start_index < 0:
            start_index = 0
        data_to_average = y_array[start_index:end_index]
        moving_avg = math.ceil(sum(data_to_average) / len(data_to_average))
        data_moving_avg.append(moving_avg)
    return data_moving_avg


def new_cases_to_risk_index(new_cases):
    """  This will work for both actual and modeled data
    ACTUAL_VALUE_SCALAR = 8
    DURATION_OF_INFECTION = 14
    """
    risk_index_list = []
    population = entity_population.value
    per_million_pops = math.ceil(population / 1e6)
    for index in range(len(new_cases)):
        index_14days = index - 14
        if index_14days < 0:
            index_14days = 0
        
        index_covid_duration = index - DURATION_OF_INFECTION
        if index_covid_duration < 0:
            index_covid_duration = 0
        
        # New Cases Per Capita
        nc = new_cases[index]
        new_cases_per_capita = nc / per_million_pops
        
        # Active Cases Per Capita
        active_cases_slice = new_cases[index_covid_duration:index]
        active_cases = sum(active_cases_slice)
        active_cases_per_capita = active_cases / per_million_pops
        
        # Chance 1 Person Infected
        chance_one_person_infected = (ACTUAL_VALUE_SCALAR * active_cases) / population
        
        # 2-Week Change in New Cases
        new_cases_14days_ago = new_cases[index_14days]
        two_week_delta = new_cases[index] - new_cases_14days_ago
        if new_cases_14days_ago == 0:
            two_week_percentage = 0
        else:
            two_week_percentage = two_week_delta / abs(new_cases_14days_ago)
        
        # Calculate Risk Index
        risk_args = [
            active_cases_per_capita, 
            chance_one_person_infected, 
            new_cases_per_capita, 
            two_week_percentage
        ]
        risk_index = matt_risk_index(*risk_args)
        risk_index_list.append(risk_index)
    
    risk_index_list = np.asarray(risk_index_list)
    return risk_index_list


def matt_risk_index(active_cases_pc, chc_1person_infected, new_cases_pc, delta_cases):
    ACTIVE_CASES_WT = 1/100
    CHANCE_INFECTED_WT = 10
    NEW_CASES_WT = 1/10
    CASE_DELTA_WT = 1/10
    
    parameters = [
        ACTIVE_CASES_WT * active_cases_pc,
        CHANCE_INFECTED_WT * chc_1person_infected,
        NEW_CASES_WT * new_cases_pc,
        CASE_DELTA_WT * delta_cases,
    ]
    
    # Calculate Weighted Average
    matt_index = sum(parameters) / len(parameters)
    matt_index = math.ceil(matt_index)
    return matt_index


def date_risk_index_not_dangerous(times, risk_indices):
    danger_cutoff = 40
    goes_into_danger_zone = False if max(risk_indices) < danger_cutoff else True
    if goes_into_danger_zone is False:
        return None
    reversed_risk_indices = list(reversed(risk_indices))
    if reversed_risk_indices[0] >= danger_cutoff:
        return "In Danger Zone"
    reversed_times = list(reversed(times))
    for risk_index in reversed_risk_indices:
        if risk_index >= danger_cutoff:
            i = reversed_risk_indices.index(risk_index) - 1
            time = reversed_times[i]
            if type(time) == datetime.date:
                time = time.strftime("%-d %B, %Y")
            else:
                time = "Day {}".format(time)
            break
    timestring = "Safe on {}".format(time)
    return timestring


def date_from_string(datestring):
    """ Creates a datetime object from the string format returned from the Case 100 queries.
    
    :param datestring: A date string. It MUST be in the format YYYY-MM-DD
    :type datestring: str
    
    :return: A datetime object of the datestring
    :rtype: :class: `datetime.date`
    """
    date_format = "%Y-%m-%d"
    date_obj = datetime.datetime.strptime(datestring, date_format).date()
    return date_obj
    
    


def max_value_plotted(*all_plotted_data):
    """ Returns the maximum y-axis value being plotted in a dataset
    
    :param all_plotted_data: List of all data (in list or numpy array format) being plotted on the y-axis.
    :type all_plotted_data: list or :class: `numpy.ndarray`
    
    :return: Maximum value in the dataset
    :rtype: float
    """
    max_value = 0
    for plotted_data in all_plotted_data:
        if max(plotted_data) > max_value:
            max_value = max(plotted_data)
    return max_value


def set_xaxis_dropdown():
    """ Enables and disables the X Axis scale dropdown menu depending on which
    entities (country/state/city) are selected.
    
    :rtype: void
    """
    if entity_date_of_100th_case.value is None:
        xaxis_selector.value = "default"
        xaxis_selector.disabled = True
    else:
        xaxis_selector.disabled = False
    return


def yaxis_scalars(max_value_plotted):
    """ Calculates the y-axis scaling factor and the axis label that accompanies it. It
    is currently set to scale if the max value plotted in thousands or millions.
    
    :param max_value_plotted: The maximum value plotted on the y-axis
    :type max_value_plotted: float
    
    :return: The y-axis scaling factor and the text that accompanies it for the y-axis label
    :rtype: tuple (int, str)
    """
    millions_cutoff = 1e6
    thousands_cutoff = 1000
    if max_value_plotted >= millions_cutoff:
        yaxis_scalar = millions_cutoff
        yaxis_scalar_text = SCALAR_MILLIONS
    elif max_value_plotted >= thousands_cutoff:
        yaxis_scalar = thousands_cutoff
        yaxis_scalar_text = SCALAR_THOUSANDS
    else:
        yaxis_scalar = 1
        yaxis_scalar_text = ""
    
    return yaxis_scalar, yaxis_scalar_text


def set_best_fit_parameters(obj):
    """ Event handler for when the "Calculate Best Fit Data" button
    is clicked. This function sets the value of the R Naught sliders
    (both the range and individual) as well as the Percent of the
    Population text input.
    
    :rtype: void
    """
    display_data_loading("Calculating Best Fit Parameters...")
    all_T_actual = get_actual_data()
    t_max = len(all_T_actual)
    t_override = np.arange(0, t_max, 1)
    percent_infected_range = np.arange(0.1, 50, 0.1)
    rnaught_rng = np.arange(1, 2, 0.1)
    
    closest_hits = ClosestHits(t_max-1)
    best_fits = BestFitOutput(t_max-1)
    
    for p in percent_infected_range:
        for rnot in rnaught_rng:
            t, S, I, R, recovered, dead, all_T_model, new_cases = generate_sir_data(
                number_of_days_widget, 
                entity_population.value,
                p,
                rnot,
                f=0,
                t=t_override
            )
            
            for i in range(1, t_max):
                actual_segment = Segment(all_T_actual[i-1], all_T_actual[i])
                model_segment = Segment(all_T_model[i-1], all_T_model[i])
                delta = SegmentDelta(actual_segment, model_segment)
                
                # Match All 3
                index = i - 1
                if delta.T_min < closest_hits.T_min[i-1] and delta.T_max < closest_hits.T_max[i-1] and delta.slope < closest_hits.slope[i-1]:
                    closest_hits.T_min[i-1] = delta.T_min
                    closest_hits.T_max[i-1] = delta.T_max
                    closest_hits.slope[i-1] = delta.slope
                    
                    best_fits.rnaughts[i-1] = round(rnot, 1)
                    best_fits.percents_infected[i-1] = round(p, 2)
            
    # Set Widget Values
    percent_of_population_infected.value = best_fits.avg_percent_infected
    rnaught_slider.value = best_fits.avg_rnaught
    rnaught_range.value = [best_fits.avg_rnaught - 0.1, best_fits.avg_rnaught + 0.2]
    yaxis_selector.value = "total"
    clear_data_loading()
    return  


def sir_plot_one_entity(obj):
    """ Plots a SIR plot for one country/city/state, in the "Single Entity" tab below
    
    :param obj: A dummy variable needed to pass to the event handler
    :type obj: object
    
    :return: None
    """
    # Initialize data and solve the differential equations
    day100 = entity_date_of_100th_case.value
    xaxis_type = xaxis_selector.value
    population = entity_population.value
    percent_infected = percent_of_population_infected.value / 100
    population_infected = population * percent_infected
    rnaught = rnaught_slider.value
    t, S, I, R, recovered, dead, total_cases, new_cases = generate_sir_data(
        number_of_days_widget, 
        population,
        percent_of_population_infected.value,
        rnaught
    )
    max_val_plotted = max_value_plotted(S, I, recovered, dead)
    yaxis_scalar, yaxis_scalar_text = yaxis_scalars(max_val_plotted)
    name = entity_name()
    
    # Generate x-axis data
    if (xaxis_type == "default" and day100) or xaxis_type == "date":
        x_data = x_axis_dates(t, day100)
        x_label = X_LABEL_DATE
        x_type_kwargs = X_TYPE_KWARGS
    elif (xaxis_type == "default" and not day100) or xaxis_type == "case100":
        x_data = t
        x_label = "Days Since 100th Case"
        x_type_kwargs = {}
    
    # Initialize Plot
    output_notebook(hide_banner=True)
    ttl = Title()
    ttl.text = "{}: {}".format(TITLE_ROOT, name)
    
    # Write plot to output
    with out:
        clear_output()
        p = figure(plot_height=PLOT_HEIGHT, plot_width=PLOT_WIDTH, **x_type_kwargs)
        p.line(x_data, S/yaxis_scalar, color="blue", legend_label='Susceptible')
        p.line(x_data, I/yaxis_scalar, color="orange", legend_label='Infected')
        p.line(x_data, recovered/yaxis_scalar, color="green", legend_label='Recovered')
        p.line(x_data, dead/yaxis_scalar, color="red", legend_label='Dead')
        p.line(x_data, total_cases/yaxis_scalar, color="darkcyan", legend_label="Total Cases")
        p.xaxis.axis_label = x_label
        p.yaxis.axis_label = "{} {}".format(Y_LABEL_PEOPLE, yaxis_scalar_text)
        p.title = ttl
        show(p)

        
def plot_multiple_entities(obj):
    """ Plots a SIR plot for multiple countries/cities/states, in the "Multiple Entities" tab below
    
    :param obj: A dummy variable needed to pass to the event handler
    :type obj: object
    
    :return: None
    """
    # Initialize variables and plot parameters
    query_string_variable = multiple_entity_type_selector.value.lower()
    rnaught = rnaught_slider.value
    colors = itertools.cycle(palette)
    percent_infected = percent_of_population_infected.value / 100
    
    # Initialize plot output
    output_notebook(hide_banner=True)
    ttl = Title()
    ttl.text = TITLE_ROOT
    plotted_data = []
    max_values = []
    names = []
    
    # Set Y Axis Label Root
    if yaxis_selector.value == "infected":
        ylabel_root = Y_LABEL_INFECTED
    elif yaxis_selector.value == "total":
        ylabel_root = Y_LABEL_TOTAL
    elif yaxis_selector.value == "new":
        ylabel_root = Y_LABEL_NEW
    
    # Solve differential equations
    for entity_id in multiple_entity_selector.value:
        json_url = '{}/all-entity-data.php?{}={}'.format(ROOT_URL, query_string_variable, entity_id)
        for r in multiple_entity_selector.options:
            if r[1] == entity_id:
                name = r[0]
                names.append(name)
                break
        with urllib.request.urlopen(json_url) as response:
            json_data = json.loads(response.read())
        population = int(json_data['population'])
        population_infected = population * percent_infected
        t, S, I, R, recovered, dead, total_cases, new_cases = generate_sir_data(
            number_of_days_widget, 
            population,
            percent_of_population_infected.value,
            rnaught
        )
        if yaxis_selector.value == "infected":
            data = I
        elif yaxis_selector.value == "total":
            data = total_cases
        elif yaxis_selector.value == "new":
            data = new_cases
        max_val_plotted = max_value_plotted(data)
        plotted_data.append(data)
        max_values.append(max_val_plotted)

    yaxis_scalar, yaxis_scalar_text = yaxis_scalars(max(max_values))
    
    # Generate Plot
    with out:
        clear_output()
        p = figure(plot_height=PLOT_HEIGHT, plot_width=PLOT_WIDTH)
        
        for I, name in zip(plotted_data, names):
            p.line(t, I/yaxis_scalar, color=next(colors), legend_label=name)
            
        p.xaxis.axis_label = X_LABEL_CASE
        p.yaxis.axis_label = "{} {}".format(ylabel_root, yaxis_scalar_text)
        p.title = ttl
        show(p)
        

def plot_multiple_rnaughts(obj):
    """ Plots a SIR plot for multiple R Naught values, in the "Multiple Multiple R Naughts" tab below
    
    :param obj: A dummy variable needed to pass to the event handler
    :type obj: object
    
    :return: None
    """
    global multiple_r0_plot_data
    multiple_ro_plot_data = {}
    matplotlib_output_parameters = ["total", "new", "riskindex"]
    
    # Define x-axis parameters
    day100 = entity_date_of_100th_case.value
    xaxis_type = xaxis_selector.value
    
    # Get data from user input menus and sliders
    population = entity_population.value
    population_density_factor = ((population_density.value/1000) + 1)
    percent_infected = (percent_of_population_infected.value * population_density_factor) / 100
    population_infected = population * percent_infected
    name = entity_name()
    rnaught_limits = rnaught_range.value
    
    x = rnaught_limits[0]
    rnaughts = []
    while x < rnaught_limits[1]:
        rnaughts.append(round(x, 1))
        x += 0.1
    
    # Set Y Axis Labels
    if yaxis_selector.value == "infected":
        ylabel_root = Y_LABEL_INFECTED
    elif yaxis_selector.value == "total":
        ylabel_root = Y_LABEL_TOTAL
    elif yaxis_selector.value == "new":
        ylabel_root = Y_LABEL_NEW
    elif yaxis_selector.value == "riskindex":
        ylabel_root = Y_LABEL_RISKINDEX
    
    # Initialize plot output
    output_notebook(hide_banner=True)
    ttl = Title()
#     if len(rnaughts) == 1:
#         title_text = "{}: {} - R Naught = {}".format(TITLE_ROOT, name, round(rnaughts[0], 1))
#     else:
#         title_text = "{}: {} - R Naught {} to {}".format(TITLE_ROOT, name, round(rnaughts[0], 1), round(rnaughts[-1], 1))
    title_text = "{}: {}".format(TITLE_ROOT, name)
    ttl.text = title_text
    colors = itertools.cycle(palette)
    plotted_data = []
    max_values = []
    
    # Solve differential equations
    for r_not in rnaughts:
        t, S, I, R, recovered, dead, total_cases, new_cases = generate_sir_data(
            number_of_days_widget, 
            population, 
            percent_of_population_infected.value,
            r_not
        )
        
        if (xaxis_type == "default" and day100) or xaxis_type == "date":
            x_data = x_axis_dates(t, day100)
            x_label = X_LABEL_DATE
            x_type_kwargs = X_TYPE_KWARGS
        elif (xaxis_type == "default" and not day100) or xaxis_type == "case100":
            x_data = t
            x_label = "Days Since 100th Case"
            x_type_kwargs = {}
        
        # Store data globally so we can plot it
        normalized_infected = new_cases / (population/1e6)
        multiple_r0_plot_data[round(r_not, 1)] = {
            'infected': I.tolist(),
            'normalized_infected': normalized_infected.tolist(),
            'new_cases': new_cases.tolist(),
            'total_cases': total_cases.tolist(),
            'timestamps': x_data.tolist(),
        }
        
        if yaxis_selector.value == "infected":
            data = I
        elif yaxis_selector.value == "total":
            data = total_cases
        elif yaxis_selector.value == "new":
            data = new_cases
        elif yaxis_selector.value == "riskindex":
            data = new_cases_to_risk_index(new_cases)
        
        max_val_plotted = max_value_plotted(data)
        plotted_data.append(data)
        max_values.append(max_val_plotted)    
    yaxis_scalar, yaxis_scalar_text = yaxis_scalars(max(max_values))
    
    with out:
        clear_output()
        p = figure(plot_height=PLOT_HEIGHT, plot_width=PLOT_WIDTH, **x_type_kwargs)
        
        # Instantiate Matplotlib figure here
        if SAVE_PLOTS_TO_IMG and yaxis_selector.value in matplotlib_output_parameters:
            mpl_legend_data = []
            fig, ax = plt.subplots()
        
        # Plot Risk Index "Danger Zone" (Bokeh Only)
        if yaxis_selector.value == "riskindex":
            hline = Span(location=40, dimension='width', line_color='firebrick', line_width=2)
            p.add_layout(hline)
        
        #  Plot the data for each R Naught value
        for I, r_not in zip(plotted_data, rnaughts):
            legend_lbl = "R0 = {}".format(round(r_not, 1))
            
            # If risk index, mark on legend when safe
            if yaxis_selector.value == "riskindex":
                d = date_risk_index_not_dangerous(x_data, I/yaxis_scalar)
                if d:
                    legend_lbl = "{} ({})".format(legend_lbl, d)
            
            p.line(x_data, I/yaxis_scalar, color=next(colors), legend_label=legend_lbl)
            
            # Add data to matplotlib figure
            if SAVE_PLOTS_TO_IMG and yaxis_selector.value in matplotlib_output_parameters:
                q, = plt.plot(x_data, I/yaxis_scalar, linewidth=0.5, label=legend_lbl)
                mpl_legend_data.append(q)
        
        if yaxis_selector.value in matplotlib_output_parameters:
            actual_data = get_actual_data()
            p.line(x_data[:len(actual_data)], actual_data/yaxis_scalar, color="dodgerblue", legend_label="Actual Data", line_width=3, line_alpha=0.6)
            
            if SAVE_PLOTS_TO_IMG:
                # Add data to matplotlib figure
                q, = plt.plot(x_data[:len(actual_data)], actual_data/yaxis_scalar, 'b-', linewidth=2, label="Actual Data", alpha=0.6)
                mpl_legend_data.append(q)

                # Plot Risk Index "Danger Zone" (Matplotlib)
                if yaxis_selector.value == "riskindex":
                    ax.axhline(y=40, linewidth=1.5, color="#CC0000")
            
        y_label = "{} {}".format(ylabel_root, yaxis_scalar_text)
        p.xaxis.axis_label = x_label
        p.yaxis.axis_label = y_label # "{} {}".format(ylabel_root, yaxis_scalar_text)
        p.legend.location = "top_left"
        p.title = ttl
        show(p)
        
    # Use MATPLOTLIB to save the images (Country and State Only)
    if SAVE_PLOTS_TO_IMG and yaxis_selector.value in matplotlib_output_parameters:
        state_id = int(state_selector.value)
        country_id = int(country_selector.value)
        today = datetime.date.today().strftime("%Y-%m-%d")
        img_directory = "model-plots/{}".format(today)
        if not os.path.exists(img_directory):
            os.makedirs(img_directory)
        entity_index = 0 if state_id > 0 else -1
        statef = name.split(", ")[0].lower().replace(" ", "-")
        img_fpath = "{}/{}.png".format(img_directory, statef)
        
        date_format = mdates.DateFormatter("%b '%y")
        ax.xaxis.set_major_formatter(date_format)
        fig.set_size_inches(14, 7)
        plt.legend(handles=mpl_legend_data)
        ax.grid()
        plt.xlabel(x_label)
        plt.ylabel(y_label)
        plt.title(ttl.text)
        
        ax.annotate(
            "Model Run: {}".format(datetime.date.today().strftime("%e %B, %Y")),
            xy=(0.5, 0), 
            xycoords=('axes fraction', 'figure fraction'),
            xytext=(0, 10), 
            textcoords='offset points',
            size=8, ha='center', va='bottom'
        )
        
#         if state_id > 0 and country_id == 190:
#             restriction_string = social_distancing_restrictions_label_state(state_id)
#             at = AnchoredText(restriction_string, loc='lower right')
#             # at.patch.set_boxstyle("round,pad=0.,rounding_size=0.2")
#             ax.add_artist(at)
        
        fig.savefig(img_fpath)
        plt.close()
        
    return
            
        

        
def plot_multiple_f_values(obj):
    """ Plots a SIR plot for multiple R Naught values, in the "Multiple Multiple R Naughts" tab below
    
    :param obj: A dummy variable needed to pass to the event handler
    :type obj: object
    
    :return: None
    """
    # Define x-axis parameters
    day100 = entity_date_of_100th_case.value
    xaxis_type = xaxis_selector.value
    
    # Get data from user input menus and sliders
    population = entity_population.value
    percent_infected = percent_of_population_infected.value / 100
    population_infected = population * percent_infected
    name = entity_name()
    rnaught = rnaught_slider.value
    f_range_limits = f_range.value
    fs = np.arange(f_range_limits[0], f_range_limits[1] + 0.1, f_step.value)
    
    # Set Y Axis Labels
    if yaxis_selector.value == "infected":
        ylabel_root = Y_LABEL_INFECTED
    elif yaxis_selector.value == "total":
        ylabel_root = Y_LABEL_TOTAL
    elif yaxis_selector.value == "new":
        ylabel_root = Y_LABEL_NEW
    
    # Initialize plot output
    output_notebook(hide_banner=True)
    ttl = Title()
    ttl.text = "{}: {} - Percentage of Population Social Distancing".format(TITLE_ROOT, name)
    colors = itertools.cycle(palette)
    plotted_data = []
    max_values = []
    
    # r_not is R Naught at 0% social distancing
#     if population_density.value > 0:
#         r_not = ((population_density.value/1000) + 1) * rnaught_slider.value
#         # r_not = ((population_density.value/10000) + 1) * rnaught_slider.value * 5
#     else:
#         r_not = rnaught_slider.value * 5
    r_not = rnaught_slider.value * 5
    
    # Solve differential equations
    for f in fs:
        # Scale the f value to account for interacting with family, going to grocery store, etc
        f = 0.75 * f
        population_percent = 1 - f/1000   # Note this is really f/10.
        
        # Solve the ODE's and set the axis labels
        t, S, I, R, recovered, dead, total_cases, new_cases = generate_sir_data(
            number_of_days_widget, 
            population_infected,
            population_percent,
            r_not, 
            f
        )
        if (xaxis_type == "default" and day100) or xaxis_type == "date":
            x_data = x_axis_dates(t, day100)
            x_label = X_LABEL_DATE
            x_type_kwargs = X_TYPE_KWARGS
        elif (xaxis_type == "default" and not day100) or xaxis_type == "case100":
            x_data = t
            x_label = "Days Since 100th Case"
            x_type_kwargs = {}
        
        if yaxis_selector.value == "infected":
            data = I
        elif yaxis_selector.value == "total":
            data = total_cases
        elif yaxis_selector.value == "new":
            data = new_cases
        
        max_val_plotted = max_value_plotted(data)
        plotted_data.append(data)
        max_values.append(max_val_plotted)    
    yaxis_scalar, yaxis_scalar_text = yaxis_scalars(max(max_values))
    
    with out:
        clear_output()
        p = figure(plot_height=PLOT_HEIGHT, plot_width=PLOT_WIDTH, **x_type_kwargs)
        
        #  Plot the data for each R Naught value
        for I, f in zip(plotted_data, fs):
            p.line(x_data, I/yaxis_scalar, color=next(colors), legend_label="{}%".format(int(f)))
        
        if yaxis_selector.value in ["total", "new"]:
            actual_data = get_actual_data()
            p.line(x_data[:len(actual_data)], actual_data/yaxis_scalar, color="dodgerblue", legend_label="Actual Data", line_width=3, line_alpha=0.6)
        
        p.xaxis.axis_label = x_label
        p.yaxis.axis_label = "{} {}".format(ylabel_root, yaxis_scalar_text)
        p.title = ttl
        show(p)

        
def relax_social_distancing(obj):
    """ Plots a SIR plot for relaxing social distancing values, in the "Relax Social Dist" tab below
    
    :param obj: A dummy variable needed to pass to the event handler
    :type obj: object
    
    :return: None
    """
    # Define x-axis parameters
    day100 = entity_date_of_100th_case.value
    xaxis_type = xaxis_selector.value
    
    # Get data from user input menus and sliders
    population = entity_population.value
    population_scalar = percent_of_population_infected.value
    population *= population_scalar
    #percent_infected = percent_of_population_infected.value / 100
    #population_infected = population * percent_infected
    name = entity_name()
    r_not = rnaught_slider.value * 5
    starting_f = f_selector.value * 0.75
    ending_f = post_sd_relaxation_percentage.value * 0.75
    f_diff = f_selector.value - post_sd_relaxation_percentage.value
    action = "Relaxing" if f_diff > 0 else "Restricting"
    f_diff = abs(f_diff)
    datestring = relax_sd_date.value.strftime("%e %B %Y")
    
    # Set Y Axis Labels
    if yaxis_selector.value == "infected":
        ylabel_root = Y_LABEL_INFECTED
    elif yaxis_selector.value == "total":
        ylabel_root = Y_LABEL_TOTAL
    elif yaxis_selector.value == "new":
        ylabel_root = Y_LABEL_NEW
    
    # Initialize plot output
    output_notebook(hide_banner=True)
    ttl = Title()
    ttl.text = "{}: {} - {} Social Distancing By {}% on {}".format(TITLE_ROOT, name, action, f_diff, datestring)
    # colors = itertools.cycle(palette)
    
    # Initialize Arrays to Hold Data
    all_t = []
    all_S = []
    all_I = []
    all_R = []
    all_recovered = []
    all_dead = []
    all_total_cases = []
    all_new_cases = []
    
    raw_t = np.arange(0, number_of_days_widget.value)
    # Add 14 to account for 2 week lag
    t_break_index = (relax_sd_date.value - entity_date_of_100th_case.value).days + 14
    t_sections = [
        raw_t[:t_break_index], 
        raw_t[t_break_index-1:],
    ]
    
    fs = [starting_f, ending_f]
    
    i0 = I0
    r0 = R0
    
    for t_section, f in zip(t_sections, fs):
        percent_infected = (1 - f/100)
        # population_infected = population * percent_infected
        t, S, I, R, recovered, dead, total_cases, new_cases = generate_sir_data(
            number_of_days_widget, 
            population,
            percent_infected,
            r_not, 
            f,
            t=t_section, I0=i0, R0=r0
        )
        
        if t_section[0] > 0:
            t = t[1:]
            S = S[1:]
            I = I[1:]
            R = R[1:]
            recovered = recovered[1:]
            dead = dead[1:]
            total_cases = total_cases[1:]
            new_cases = new_cases[1:]
        all_t.extend(t)
        all_S.extend(S)
        all_I.extend(I)
        all_R.extend(R)
        all_recovered.extend(recovered)
        all_dead.extend(dead)
        all_total_cases.extend(total_cases)
        all_new_cases.extend(new_cases)
        
        i0 = all_I[-1]
        r0 = all_R[-1]
    
    # Generate Control (No Change in Restrictions Curve)
    percent_infected = (1 - starting_f/100)
    # population_infected = population * percent_infected
    ctrl_t, ctrl_S, ctrl_I, ctrl_R, ctrl_recovered, ctrl_dead, ctrl_total_cases, ctrl_new_cases = generate_sir_data(
        number_of_days_widget, 
        population,
        percent_infected,
        r_not, 
        starting_f,
        # t=t_section, I0=i0, R0=r0
    )
    
    # Solve differential equations
    if (xaxis_type == "default" and day100) or xaxis_type == "date":
        x_data = x_axis_dates(all_t, day100)
        x_label = X_LABEL_DATE
        x_type_kwargs = X_TYPE_KWARGS
    elif (xaxis_type == "default" and not day100) or xaxis_type == "case100":
        x_data = all_t
        x_label = "Days Since 100th Case"
        x_type_kwargs = {}

    if yaxis_selector.value == "infected":
        data = all_I
        control = ctrl_I
    elif yaxis_selector.value == "total":
        data = all_total_cases
        control = ctrl_total_cases
    elif yaxis_selector.value == "new":
        data = all_new_cases
        control = ctrl_new_cases
    
    data = np.asarray(data) 
    yaxis_scalar, yaxis_scalar_text = yaxis_scalars(max(data))
    
    with out:
        clear_output()
        p = figure(plot_height=PLOT_HEIGHT, plot_width=PLOT_WIDTH, **x_type_kwargs)
        p.line(x_data, control/yaxis_scalar, color="green", legend_label="No Social Distancing {}".format(action))
        p.line(x_data, data/yaxis_scalar, color="red", legend_label="{} Social Distancing {}%".format(action, f_diff))
        if yaxis_selector.value in ["total", "new"]:
            actual_data = get_actual_data()
            p.line(x_data[:len(actual_data)], actual_data/yaxis_scalar, color="dodgerblue", legend_label="Actual Data", line_width=3, line_alpha=0.6)
        legend_location = "bottom_right" if yaxis_selector.value == "total" else "top_right"
        p.xaxis.axis_label = x_label
        p.yaxis.axis_label = "{} {}".format(ylabel_root, yaxis_scalar_text)
        p.legend.location = legend_location
        p.title = ttl
        show(p)

        
def plot_custom_data(obj):
    """ Plots a SIR plot for a custom scenario defined in the "Custom Scenario" tab below
    
    :param obj: A dummy variable needed to pass to the event handler
    :type obj: object
    
    :return: None
    """
    # Get data from user input menus and sliders
    day100 = custom_date_widget.value
    population = population_widget.value * 1e6
    percent_infected = percent_of_population_infected.value / 100
    population_infected = population * percent_infected
    rnaught = rnaught_slider.value
    
    # Solve the differential equations
    t, S, I, R, recovered, dead, total_cases, new_cases = generate_sir_data(
        number_of_days_widget, 
        population,
        percent_of_population_infected.value,
        rnaught
    )
    max_val_plotted = max_value_plotted(S, I, recovered, dead)
    yaxis_scalar, yaxis_scalar_text = yaxis_scalars(max_val_plotted)
    
    # Define x-axis parameters
    if day100:
        x_data = x_axis_dates(t, day100)
        x_label = X_LABEL_DATE
        x_type_kwargs = X_TYPE_KWARGS
    else:
        x_data = t
        x_label = X_LABEL_CASE
        x_type_kwargs = {}
    
    # Initialize Plot
    output_notebook(hide_banner=True)
    title_customization = custom_text_label_widget.value if custom_text_label_widget.value else "Custom Scenario"
    ttl = Title()
    ttl.text = "{}: {}".format(TITLE_ROOT, title_customization)

    with out:
        clear_output()
        
        # Generate Plot
        p = figure(plot_height=PLOT_HEIGHT, plot_width=PLOT_WIDTH, **x_type_kwargs)
        p.line(x_data, S/yaxis_scalar, color="blue", legend_label='Susceptible')
        p.line(x_data, I/yaxis_scalar, color="orange", legend_label='Infected')
        p.line(x_data, recovered/yaxis_scalar, color="green", legend_label='Recovered')
        p.line(x_data, dead/yaxis_scalar, color="red", legend_label='Dead')
        p.line(x_data, total_cases/yaxis_scalar, color="darkcyan", legend_label="Total Cases")
        p.xaxis.axis_label = x_label
        p.yaxis.axis_label = "{} {}".format(Y_LABEL_PEOPLE, yaxis_scalar_text)
        p.title = ttl
        show(p)
    

def generate_sir_data(num_days_widget, population, percent_infected, r_not, f=0, **overrides):
    """ Solves the system of ordinary differential equations for the SIR model and returns a tuple
    of the solution in a format that is ready to plot.
    
    :param num_days_widget: The widget object in the user input that states how many days to model
    :type num_days_widget: :class: `ipywidgets.IntSlider`
    :param population: The total population of the entity being modeled
    :type population: int
    :param percent_infected: The percentage of the population that becomes infected
    :type percent_infected: int
    :param r_not: The R Naught value
    :type r_not: float
    :param f: The percent of the population complying with social distancing
    :type f: float
    :param t_override: A numpy array of t values that will override the num_days_widget value
    :type t_override: :class: `numpy.arange`
    
    :return: A tuple (numpy array) of time steps, susceptible, infected, removed, recovered, 
        and dead from the modeled outbreak
    :rtype: tuple
    """
    # Set initial values
    percent_infected = percent_infected / 100
    scaled_population = population * percent_infected
    s_scalar = population * (1 - percent_infected)
    i_i = overrides["I0"] if "I0" in overrides.keys() else I0
    r_i = overrides["R0"] if "R0" in overrides.keys() else R0
    S0 = scaled_population - i_i - r_i
    t = overrides["t"] if "t" in overrides.keys() else np.arange(0, num_days_widget.value)
    y0 = S0, i_i, r_i
    beta = r_not * GAMMA
    
    integrated = odeint(sir_model, y0, t, args=(scaled_population, beta, GAMMA, f))
    S, I, R = integrated.T
    S += s_scalar
    death_rate_decimal = DEATH_RATE / 100
    recovered = R * (1 - death_rate_decimal)
    dead = R * death_rate_decimal
    total_cases = I + R
    
    yesterday_total_cases = 100
    new_cases = []
    for cases in total_cases:
        today_new_cases = cases - yesterday_total_cases
        new_cases.append(today_new_cases)
        yesterday_total_cases = cases
    
#     # Calculate 7-Day Moving Average for New Cases
#     new_cases_7day_avg = []
#     for i in range(len(new_cases)):
#         end_index = 1 if i == 0 else i
#         start_index = i - 7
#         if start_index < 0:
#             start_index = 0
#         data_to_average = new_cases[start_index:end_index]
#         moving_avg = math.ceil(sum(data_to_average) / len(data_to_average))
#         new_cases_7day_avg.append(moving_avg)

    new_cases = np.asarray(new_cases)
        
    return t, S, I, R, recovered, dead, total_cases, new_cases


def display_data_loading(text):
    """ Displays a notice in the widget interface that the data is loading.
    
    :param text: The text to display
    :type text: str
    """
    entity_data_loading.value = "<p style='color:#C00;'><b>{}</b></p>".format(text)


def clear_data_loading():
    """ Clears/hides the data loading notice """
    entity_data_loading.value = ""

    
def load_actual_country_data():
    """ """
    with urllib.request.urlopen('{}/country-plot-data.php'.format(ROOT_URL)) as response:
        json_data = json.loads(response.read())
        all_data = json_data['data']
        return all_data

    
def load_actual_state_data():
    """ """
    countriesWithStateData = [190, 10, 26, 33, 37, 38, 39, 66, 79, 87, 115, 127, 134, 140, 146, 166, 171, 187]
    all_data = {}
    for country in countriesWithStateData:
        with urllib.request.urlopen('{}/state-plot-data.php?country={}'.format(ROOT_URL, country)) as response:
            json_data = json.loads(response.read())
            state_data = json_data['data']
            for state_id in state_data.keys():
                all_data[state_id] = state_data[state_id]
    return all_data   


def load_countries():
    """ Generates a list of countries that will be populated in the dropdown and selector menus
    
    :return: A list of countries (name, value) that will be put into the dropdown and selector menus
    :rtype: list
    """
    with urllib.request.urlopen('{}/all-entities-json.php'.format(ROOT_URL)) as response:
        json_data = json.loads(response.read())
        all_countries = json_data['country']
    options=[['-- Select a Country --', '-1']]
    options.extend(all_countries)
    return options


def load_states(change):
    """ Populates the state and cities dropdown and selector menus when the country selector's value
    changes, with all states/cities in the country that is selected.
    
    NOTE: Only states/cities that have population data in the database are displayed.
    
    :param change: A dictionary that is automatically passed to the function when the value of the
        country dropdown menu changes
    :type change: dict
    
    :return: None
    """
    if change['type'] == 'change' and change['name'] == 'value':
        display_data_loading("Loading State List, Population, and 100th Case Data")
        country_id = country_selector.value
        
        # Obtain Data from Database
        json_url = '{}/all-entities-json.php?country={}'.format(ROOT_URL, country_id)
        with urllib.request.urlopen(json_url) as response:
            json_data = json.loads(response.read())
            all_states = json_data['state']
            all_cities = json_data['city']
        
        # Populate the states dropdown and/or selector menus
        if all_states == []:
            state_selector.options = NO_DATA_AVAILABLE
            state_selector.disabled = True
        else:
            options=[['-- Select a State/Province --', '-1']]
            options.extend(all_states)
            state_selector.disabled = False
            state_selector.options = options
        
        # Populate the cities dropdown and/or selector menus
        if all_cities == []:
            city_selector.options = NO_DATA_AVAILABLE
            city_selector.disabled = True
        else:
            city_options=[['-- Select a City --', '-1']]
            city_options.extend(all_cities)
            city_selector.disabled = False
            city_selector.options = city_options
        
        # Populate the population field
        json_url = '{}/all-entity-data.php?country={}'.format(ROOT_URL, country_id)
        with urllib.request.urlopen(json_url) as response:
            json_data = json.loads(response.read())
        entity_population.value = int(json_data['population'])
        entity_date_of_100th_case.value = date_from_string(json_data['case100']) if json_data['case100'] else None
        population_density.value = int(json_data['density']) if json_data['density'] else 0
        set_xaxis_dropdown()
        
        # Multiple Entities Fields
        # If no country is selected, states do not display, but it will display every city
        # in the database that has population data.
        if user_input_tabs.selected_index == 1:
            if multiple_entity_type_selector.value == "City":
                display_data_loading("Loading Cities...")
                query_string = "?country={}&include_state=true".format(country_id)
                load_options_from_json('all-entities-json', query_string, 'city', multiple_entity_selector)
            elif multiple_entity_type_selector.value == "State":
                display_data_loading("Loading States...")
                query_string = "?country={}".format(country_id)
                load_options_from_json('all-entities-json', query_string, 'state', multiple_entity_selector)
        clear_data_loading()


def load_options_from_json(php_file, query_string, json_key, widget):
    """ Retrieves country/state/city data from the database (JSON format) and populate the
    widget's dropdown and/or selector options.
    
    :param php_file: The name of the PHP file, without the ".php" extension from which this 
        function obtains the data from the database
    :type php_file: str
    :param query_string: The full query string for the PHP file, including the "?"
    :type query_string: str
    :param json_key: The entity type key (country/city/state) that you want to populate
    :type json_key: str
    :param widget: The widget object that you wish to populate
    :type widget: :class: `ipywidgets.Dropdown` or :class: `ipywidgets.Select` 
        or :class: `ipywidgets.SelectMultiple`
    
    :return: None
    """
    json_url = '{}/{}.php{}'.format(ROOT_URL, php_file, query_string)
    with urllib.request.urlopen(json_url) as response:
        json_data = json.loads(response.read())  
        options = json_data[json_key]
    widget.options = options

    
def load_cities(change):
    """ Populates the cities dropdown and selector menus when the state selector's value
    changes, with all cities in the state that is selected.
    
    NOTE: Only cities that have population data in the database are displayed.
    
    :param change: A dictionary that is automatically passed to the function when the value of the
        state dropdown menu changes
    :type change: dict
    
    :return: None
    """
    if change['type'] == 'change' and change['name'] == 'value':
        if int(state_selector.value) < 0:
            load_states(change)
            return 
        
        display_data_loading("Loading City List, Population, and 100th Case Data")
        
        # Get selected country and state
        country_id = country_selector.value
        state_id = state_selector.value
        
        # Load data from database
        json_url = '{}/all-entities-json.php?country={}&state={}'.format(ROOT_URL, country_id, state_id)
        with urllib.request.urlopen(json_url) as response:
            json_data = json.loads(response.read())  
            all_cities = json_data['city']
        
        # Populate the cities dropdown and/or selector
        if all_cities == []:
            city_selector.options = NO_DATA_AVAILABLE
            city_selector.disabled = True
        else:
            options=[['-- Select a City --', '-1']]
            options.extend(all_cities)
            city_selector.disabled = False
            city_selector.options = options
        
        # Populate the population and date of 100th case field
        json_url = '{}/all-entity-data.php?state={}'.format(ROOT_URL, state_id)
        with urllib.request.urlopen(json_url) as response:
            json_data = json.loads(response.read())
        entity_population.value = int(json_data['population']) if json_data['population'] else 0
        if json_data['case100']:
            case100_date = date_from_string(json_data['case100']) # datetime.datetime.strptime(json_data['case100'], "%Y-%m-%d")
            entity_date_of_100th_case.value = case100_date
        else:
            entity_date_of_100th_case.value = None
        population_density.value = int(json_data['density']) if json_data['density'] else 0
        set_xaxis_dropdown()
        clear_data_loading()


def city_data(change):
    """ Populates the population and date of 100th case fields when the selected city changes
    
    :param change: A dictionary that is automatically passed to the function when the value of the
        city dropdown menu changes
    :type change: dict
    
    :return: None
    """
    if change['type'] == 'change' and change['name'] == 'value':
        if int(city_selector.value) < 0:
            load_cities(change)
            return            
        
        display_data_loading("Loading Population, and 100th Case Data")
        
        # Get selected city
        city_id = city_selector.value
        
        # Load data from database
        json_url = '{}/all-entity-data.php?city={}'.format(ROOT_URL, city_id)
        with urllib.request.urlopen(json_url) as response:
            json_data = json.loads(response.read())
            
        # Populate population and date of 100th case fields
        entity_population.value = int(json_data['population']) if json_data['population'] else 0
        entity_date_of_100th_case.value = date_from_string(json_data['case100']) if json_data['case100'] else None
        population_density.value = int(json_data['density']) if json_data['density'] else 0
        set_xaxis_dropdown()
        clear_data_loading()
        
        
def multiple_entity_type_change(change):
    """ Event handler for when the "Entity Type" dropdown on the Multiple Entities page changes
    
    :param change: A dictionary that is automatically passed to the function when the value of the
        city dropdown menu changes
    :type change: dict
    
    :return: None
    """
    if change['type'] == 'change' and change['name'] == 'value':
        country_id = int(country_selector.value)
        
        # Country Selected: Populate with Countries
        if multiple_entity_type_selector.value == "Country":
            multiple_entity_selector.options = country_options[1:]
        
        # State Selected: Populate with States if country is selected
        elif multiple_entity_type_selector.value == "State":
            if country_id > 0:
                query_string = "?country={}".format(country_id)
                load_options_from_json('all-entities-json', query_string, 'state', multiple_entity_selector)
            else:
                multiple_entity_selector.options = ["Please Select a Country"]
        
        # City Selected: Populate with Cities - either all cities in database or in selected country and/or state
        elif multiple_entity_type_selector.value == "City":
            query_string = "?country={}&include_state=true".format(country_id) if country_id > 0 else "?include_country=true"
            load_options_from_json('all-entities-json', query_string, 'city', multiple_entity_selector)
        
        # Set the description of the multiple entity selector to Country/State/City
        multiple_entity_selector.description = multiple_entity_type_selector.value

        
def social_distancing_restrictions_label_state(state_id):
    """ Generates the string that goes in the lower right corner of the plot showing
    when each social distancing restriction was implemented
    
    :param state_id: The unique state idenitifier
    :type state_id: int
    
    :return: A string of the text that will go in the lower right corner of the plot
    :rtype: str
    """
    state_id = str(state_id)
    sd_restrictions = ACTUAL_STATE_DATA[state_id]['sd_restrictions']
    restriction_string = ""
    first_line = True
    for restriction in sd_restrictions.values():
        dates_implemented = restriction['dates_implemented']
        dates_lifted = restriction['dates_lifted']
        for d in dates_implemented:
            dt = date_from_string(d)
            datestring = dt.strftime("%b %e")
            if first_line:
                first_line = False
            else:
                restriction_string += "\n"
            restriction_string += "{}: {}".format(restriction['name'], datestring)
            imp_index = dates_implemented.index(d)
            if imp_index < len(dates_lifted):
                date_lifted = date_from_string(dates_lifted[imp_index]).strftime("%b %e")
                restriction_string += " to {}".format(date_lifted)
    return restriction_string 

        
def clear_csv_file(change):
    """ Event handler for when the "Clear CSV" button is clicked
    
    :param change: A dictionary that is automatically passed to the function when the button
        is clicked.
    :type change: dict
    
    :return: None
    """
    csv_headers = [
        "StateID", 
        # "State", 
        "R0", 
        "ApexDateMin", 
        "ApexDateMax", 
        "Cases14DayMin",
        "Cases14DayMax",
        "Cases1MoMin",
        "Cases1MoMax",
        "ReopeningDateMin",
        "ReopeningDateMax",
    ]
    
    # Idiot Proof: Backup the Existing Model Output File
    with open(MODEL_OUTPUT_CSV, 'r') as model_file:
        data = csv.reader(model_file)
        backup_data = list(data)
    
    with open('model-plots/state-model-backup.csv', 'w') as backup_file:
        writer = csv.writer(backup_file)
        writer.writerows(backup_data)
    
    # Clear the Existing CSV
    with open(MODEL_OUTPUT_CSV, 'w') as model_file:
        writer = csv.writer(model_file)
        writer.writerow(csv_headers)
    return


def add_to_csv_file(change):
    """ Event handler for when the "Add to CSV" Button is Clicked
    
    :param change: A dictionary that is automatically passed to the function when the button
        is clicked.
    :type change: dict
    
    :return: None
    """
    actual_data = get_actual_data()
    current_num_cases = actual_data[-1]
    state_id = int(state_selector.value)
    today = datetime.datetime.combine(datetime.date.today(), datetime.datetime.min.time())
    today = today.date()
    plus1mo_year = today.year if today.month < 12 else today.year + 1
    plus1mo_month = today.month + 1 if today.month < 12 else 1
    plus1mo_day = today.day
    while plus1mo_day > 0:
        try:
            today_plus_1month = datetime.date(plus1mo_year, plus1mo_month, plus1mo_day) #, today.day)
            break
        except:
            plus1mo_day -= 1
    
    # Check that day slider goes at least 1 month into the future
    
    # Check to ensure state is not already in the CSV file
    is_in_csv_file = False
    with open(MODEL_OUTPUT_CSV, 'r') as model_file:
        data = csv.reader(model_file)
        next(data)
        for row in data:
            if int(row[0]) == state_id:
                is_in_csv_file = True
                break
    
    # Parse R Naught
    # rnaught_rng = rnaught_range.value
    rnaught_rng = [rnaught_range.value[0], rnaught_range.value[1]-0.1]
    r_not = round(sum(rnaught_rng)/len(rnaught_rng), 1)
    today_index = multiple_r0_plot_data[r_not]['timestamps'].index(today)
    plus1mo_index = multiple_r0_plot_data[r_not]['timestamps'].index(today_plus_1month)
    
    # Apex Max and Min
    min_key = round(r_not + 0.1, 1)
    proj_key = round(r_not, 1)
    max_key = round(r_not - 0.1, 1)

    min_list = multiple_r0_plot_data[min_key]['infected']
    min_index = min_list.index(max(min_list))
    
    proj_list = multiple_r0_plot_data[proj_key]['infected']
    proj_index = proj_list.index(max(proj_list))

    max_list = multiple_r0_plot_data[max_key]['infected']
    max_index = max_list.index(max(max_list))
    
    min_date_obj = multiple_r0_plot_data[min_key]['timestamps'][min_index]
    proj_date_obj = multiple_r0_plot_data[proj_key]['timestamps'][proj_index]
    max_date_obj = multiple_r0_plot_data[min_key]['timestamps'][max_index]
    
    if max_date_obj < min_date_obj:
        temp_min = min_date_obj
        temp_max = max_date_obj
        min_date_obj = temp_max
        max_date_obj = temp_min
    
    min_date_diff = (proj_date_obj - min_date_obj).days
    max_date_diff = (max_date_obj - proj_date_obj).days
    
    min_date = proj_date_obj - datetime.timedelta(days=min_date_diff/2)
    max_date = proj_date_obj + datetime.timedelta(days=max_date_diff/2)
    
    min_date = min_date.strftime("%Y-%m-%d")
    max_date = max_date.strftime("%Y-%m-%d")
    
    # Total Cases 14 Days From Now
    total_14day_min = math.floor(multiple_r0_plot_data[proj_key]['total_cases'][today_index + 14]/1000)
    if total_14day_min < current_num_cases/1000:
        total_14day_min = math.floor(current_num_cases/1000)
    total_14day_max = math.ceil(multiple_r0_plot_data[min_key]['total_cases'][today_index + 14]/1000)
    if total_14day_min == total_14day_max:
        total_14day_min -= 1
    
    # Total Cases 1 Month From Now
    max_key_1mo = round(r_not + 0.1, 1)
    min_key_1mo = round(r_not, 1)
    total_1mo_min = math.floor(multiple_r0_plot_data[min_key_1mo]['total_cases'][plus1mo_index]/1000)
    if total_1mo_min < current_num_cases/1000:
        total_1mo_min = math.floor(current_num_cases/1000)
    total_1mo_max = math.ceil(multiple_r0_plot_data[max_key_1mo]['total_cases'][plus1mo_index]/1000)
    if total_1mo_min == total_1mo_max:
        total_1mo_min -= 1
    
    # Date When Infections Reach less than 5 per million
    new_case_threshold = 5
    max_list = multiple_r0_plot_data[max_key]['normalized_infected']
    max_index = max_list.index(max(max_list))
    
    max_infected_list = multiple_r0_plot_data[max_key]['normalized_infected'][max_index:]
    max_reopening_index = -9999
    for d in max_infected_list:
        if d < new_case_threshold:
            max_reopening_index = max_infected_list.index(d) + max_index
            max_reopening_date = multiple_r0_plot_data[max_key]['timestamps'][max_reopening_index].strftime("%Y-%m-%d")
            break
    
    min_list = multiple_r0_plot_data[proj_key]['normalized_infected']
    min_index = min_list.index(max(min_list))
    min_infected_list = multiple_r0_plot_data[proj_key]['normalized_infected'][min_index:]
    min_reopening_index = -9999
    for d in min_infected_list:
        if d < new_case_threshold:
            min_reopening_index = min_infected_list.index(d) + min_index
            min_reopening_date = multiple_r0_plot_data[proj_key]['timestamps'][min_reopening_index].strftime("%Y-%m-%d")
            break
    
    if max_reopening_date < min_reopening_date:
        temp_min = min_reopening_date
        temp_max = max_reopening_date
        min_reopening_date = temp_max
        max_reopening_date = temp_min
    
    csv_row = [
        state_id,
        r_not,
        min_date,  # Apex Min
        max_date,  # Apex Max
        total_14day_min,
        total_14day_max,
        total_1mo_min,
        total_1mo_max,
        min_reopening_date,
        max_reopening_date,
    ]
    
    if is_in_csv_file:
        csv_output = []
        with open(MODEL_OUTPUT_CSV, 'r') as csv_file:
            reader = csv.reader(csv_file)
            # next(reader)
            is_header = True
            for row in reader:
                if is_header:
                    csv_output.append(row)
                    is_header = False
                    continue
                    
                if int(row[0]) == int(state_id):
                    csv_output.append(csv_row)
                else:
                    csv_output.append(row)
        with open(MODEL_OUTPUT_CSV, 'w') as csv_file:
            writer = csv.writer(csv_file)
            writer.writerows(csv_output)         
    else:
        with open(MODEL_OUTPUT_CSV, 'a') as csv_file:
            writer = csv.writer(csv_file)
            writer.writerow(csv_row)
        

        
################################################################################

# Define Constants
ACTUAL_VALUE_SCALAR = 8
DURATION_OF_INFECTION = 14    # days
DEATH_RATE = 2.3    # percent
GAMMA = 1 / DURATION_OF_INFECTION
I0 = 100
R0 = 0
NO_DATA_AVAILABLE = [['No Population Data Available', '-1']]
ROOT_URL = "http://covid19.matthewgove.com/json"
PLOT_HEIGHT = 400
PLOT_WIDTH = 850
TITLE_ROOT = "Matt's COVID-19 Model" # "COVID-19 Outbreak SIR Model"
SCALAR_MILLIONS = "(Millions)"
SCALAR_THOUSANDS = "(Thousands)"
MODEL_OUTPUT_CSV = "model-output-csv/state_model.csv"
SAVE_PLOTS_TO_IMG = False

X_LABEL_DATE = "Calendar Date"
X_LABEL_CASE = "Days Since 100th Case"
X_TYPE_KWARGS = {"x_axis_type": "datetime"}
Y_LABEL_PEOPLE = "Number of People"
Y_LABEL_INFECTED = "Number of Infected"
Y_LABEL_TOTAL = "Total Cases"
Y_LABEL_NEW = "New Cases"
Y_LABEL_RISKINDEX = "Matt's Risk Index"

ACTUAL_COUNTRY_DATA = load_actual_country_data()
ACTUAL_STATE_DATA = load_actual_state_data()


multiple_r0_plot_data = {}
social_distancing_restrictions = {}


# Initialize Widgets
# --------------------

# Number of Days to Plot Widget
number_of_days_widget = widgets.IntText(
    value=360,
    min=0,
    step=1,
    description="Num Days"
)

# R Naught (Single Value) Slider
rnaught_slider = widgets.FloatSlider(
    value=2.4,
    min=0,
    max=6,
    step=0.1,
    description="R Naught",
    disabled=False,
    continuous_update=False,
    readout=True,
    readout_format=".1f"
)

# f_slider = widgets.IntSlider(
#     value=50,
#     min=0,
#     max=100,
#     step=1,
#     description="Soc Dist %"
# )

# X Axis Type Dropdown Menu
xaxis_selector = widgets.Dropdown(
    options=[
        ("Set X Axis Automatically", "default"), 
        ("Calendar Date", "date"), 
        ("Days Since 100th Case", "case100")
    ],
    description="X Axis",
    disabled=True
)

# Y Axis Type Dropdown Menu
yaxis_selector = widgets.Dropdown(
    options=[ 
        ("Number of Infected", "infected"), # Plot Number of Infected by Default
        ("Total Cases", "total"),
        ("New Cases", "new"),
        ("Matt's Risk Index", "riskindex"),
    ],
    description="Y Axis",
    disabled=False
)

# Best Fit Data Button
best_fit_btn = widgets.Button(
    description="Best Fit to Observed",
    disabled=False,
    layout=widgets.Layout(margin="0 0 0 91px")
)

# Output Widget
out = widgets.Output(layout=widgets.Layout(height="450px"))

#####################################################
# Entity Selections
country_options = load_countries()

# Countries Dropdown Widget
country_selector = widgets.Dropdown(
    options=country_options,
    description="Country",
    disabled=False
)

# States Dropdown Widget
state_selector = widgets.Dropdown(
    options=[('-- Select a State/Province --', '-1')],
    description="State",
    disabled=False
)

# Cities Dropdown Widget
city_selector = widgets.Dropdown(
    options=[('-- Select a City --', '-1')],
    description="City",
    disabled=False
)

# Population Text Box Widget
entity_population = widgets.IntText(
    value=0,
    description="Population",
    disabled=True
)

# Percent of Population Infected
percent_of_population_infected = widgets.FloatText(
    value=1,
    min=0,
    max=100,
    step=0.01,
    description="% Infected"
)

# Date of 100th Case Text Box Widget
entity_date_of_100th_case = widgets.DatePicker(
    description="100th Case",
    disabled=True,
)

# Data Loading Label Widget
entity_data_loading = widgets.HTML(
    value="",
    layout=widgets.Layout(margin="0 0 0 50px")
)

# Country/State/City Dropdown Vertical Box
entity_selector = widgets.VBox([
    country_selector,
    state_selector,
    city_selector,
])

# Population and Date of 100th Case Vertical Box
entity_data = widgets.VBox([
    entity_population,
    percent_of_population_infected,
    entity_date_of_100th_case,
    entity_data_loading,
])

# All Entities Widget
entity_interface = widgets.HBox([
    entity_selector,
    entity_data,
])


#####################################################
# Single Entity

# Single Entity "Plot Data" Button
single_entity_plot_data_btn = widgets.Button(
    description="Plot Data",
    disabled=False,
    layout=widgets.Layout(margin="0 0 0 93px")
)

# Number of Days and R Naught Horizontal Box
single_entity_inputs = widgets.HBox([
    number_of_days_widget, 
    rnaught_slider,
    # f_slider,
])

single_entity_plot_row = widgets.HBox([
    xaxis_selector,
    single_entity_plot_data_btn
])

# All Single Entity Widgets
single_entity_input_widgets = widgets.VBox([
    single_entity_inputs,
    entity_interface,
    single_entity_plot_row
])


#####################################################
# Multiple Entities

# Multiple Entities "Plot Data" Button
multiple_entity_plot_data_btn = widgets.Button(
    description="Plot Data",
    disabled=False,
    layout=widgets.Layout(margin="0 0 0 93px")
)

# Country/State/City Entity Type Dropdown Menu
multiple_entity_type_selector = widgets.Dropdown(
    options=["Country", "State", "City"],
    description="Entity Type",
    disabled=False
)

# Multiple Selector Widget to Select Which Entities to Plot
multiple_entity_selector = widgets.SelectMultiple(
    options=country_options[1:],
    description="Country",
    disabled=False,
    layout=widgets.Layout(width="400px")
)

# Multiple Entity Entity Type/Country Selector Vertical Box
multiple_entity_filter = widgets.VBox([
    multiple_entity_type_selector,
    country_selector,
    entity_data_loading,
    
])

# Multiple Entity Filter/Selector Horizontal Box
multiple_entity_row = widgets.HBox([
    multiple_entity_filter,
    multiple_entity_selector
])

# Number of Days/R Naught Sliders Horizontal Box
multiple_entity_inputs = widgets.HBox([
    number_of_days_widget, 
    rnaught_slider,
])

# Last Row: Plot Data Button and instructions to select multiple entities
multiple_entity_last_row = widgets.HBox([
    yaxis_selector,
    widgets.Label(value="Hold Control or Shift to Select Multiple Entities", layout=widgets.Layout(margin="0 0 0 80px")),
])

multiple_entity_last_last_row = widgets.HBox([
    percent_of_population_infected, 
    multiple_entity_plot_data_btn
])

# Entire Multiple Entity User Interface
multiple_entity_input_widgets = widgets.VBox([
    multiple_entity_inputs, 
    multiple_entity_row,
    multiple_entity_last_row,
    # multiple_entity_plot_data_btn
    multiple_entity_last_last_row,
])

#####################################################
# Multiple R0's

# R Naught Range Selector Slider
rnaught_range = widgets.FloatRangeSlider(
    value=[1.0, 1.4],
    min=0.5,
    max=2.5,
    step=0.1,
    description="R Naught",
    disabled=False,
    continuous_update=False,
    orientation="horizontal",
    readout=True,
    readout_format=".1f"
)

# Multiple R Naught "Plot Data" Button
multiple_rnaught_plot_data_btn = widgets.Button(
    description="Plot Data",
    disabled=False,
    layout=widgets.Layout(margin="0 0 0 154px")
)

# Add to CSV Button
add_to_csv_btn = widgets.Button(
    description="Add to CSV",
    disabled=False,
    layout=widgets.Layout(margin="0 0 0 100px")
)

# Clear CSV Button
clear_csv_btn = widgets.Button(
    description="Clear CSV",
    disabled=False,
    layout=widgets.Layout(margin="0 0 0 35px")
)

# Number of Days and R Naught Range Horizontal Box
multiple_rnaught_inputs = widgets.HBox([
    number_of_days_widget, 
    rnaught_range,
    # clear_csv_btn,
])

multiple_rnaught_plot_row = widgets.HBox([
    xaxis_selector,
    yaxis_selector
])

multiple_rnaught_buttons = widgets.HBox([
    best_fit_btn,
    multiple_rnaught_plot_data_btn,
    # add_to_csv_btn,
])

# All Multiple R Naught Widgets
multiple_rnaught_input_widgets = widgets.VBox([
    multiple_rnaught_inputs, 
    entity_interface,
    multiple_rnaught_plot_row,
    multiple_rnaught_buttons
])

#####################################################
# Multiple f Values

# f Range Selector Slider
f_range = widgets.IntRangeSlider(
    value=[40, 60],
    min=0,
    max=100,
    step=5,
    description="Soc Dist %",
)

f_selector = widgets.IntSlider(
    value=30,
    min=0,
    max=100,
    step=1,
    description="Soc Dist %"
)

# f Step
f_step = widgets.IntText(
    value=5,
    description="Soc Dist Step",
    min=1,
    max=50
)

# Population Density
population_density = widgets.IntText(
    value=None,
    description="Pop Density",
    disabled=True,
    layout=widgets.Layout(width="210px")
)

# Multiple f "Plot Data" Button
multiple_f_plot_data_btn = widgets.Button(
    description="Plot Data",
    disabled=False,
    layout=widgets.Layout(margin="0 0 0 93px")
)

# damping_f_plot_data_btn = widgets.Button(
#     description="Plot Data",
#     disabled=False,
#     layout=widgets.Layout(margin="0 0 0 93px")
# )

f_row = widgets.HBox([
    f_range,
    f_step
])

# damping_f_row = widgets.HBox([
#     f_selector,
#     f_step
# ])

f_submit_row = widgets.HBox([
    xaxis_selector,
    yaxis_selector,
])

f_last_row = widgets.HBox([
    population_density,
    widgets.Label("per square km"),
    multiple_f_plot_data_btn
])

# damping_f_last_row = widgets.HBox([
#     population_density,
#     widgets.Label("per square km"),
#     damping_f_plot_data_btn
# ])

multiple_f_widgets = widgets.VBox([
    single_entity_inputs,
    f_row,
    entity_interface,
    f_submit_row,
    f_last_row
])

# damping_f_widgets = widgets.VBox([
#     single_entity_inputs,
#     damping_f_row,
#     entity_interface,
#     f_submit_row,
#     damping_f_last_row
# ])

#####################################################
# Relaxing Social Distancing Tab

# Relaxing Social Distancing "Plot Data" Button
relax_sd_plot_data_btn = widgets.Button(
    description="Plot Data",
    disabled=False,
    layout=widgets.Layout(margin="0 0 0 93px")
)

# Date Social Distancing Measures Relaxed
relax_sd_date = widgets.DatePicker(
    description="Date Relaxed",
    value=datetime.date.today()
)

# Post-Change Date Social Distancing Percentage
post_sd_relaxation_percentage = widgets.IntSlider(
    value=50,
    min=0,
    max=100,
    step=1,
    description="New SD %"
)

# Tab-Specific Widgets
relax_sd_row = widgets.HBox([
    f_selector,
    relax_sd_date,
    post_sd_relaxation_percentage,
])

# Last Row/Submit Button
relax_sd_last_row = widgets.HBox([
    population_density,
    widgets.Label("per square km"),
    relax_sd_plot_data_btn
])

# All Widgets In the Tab
relax_sd_widgets = widgets.VBox([
    single_entity_inputs,
    relax_sd_row,
    entity_interface,
    f_submit_row,
    relax_sd_last_row
])



#####################################################
# Custom Scenario

# Population Text Box
population_widget = widgets.FloatText(
    value=3.5,
    description="Population",
    disabled=False,
    layout=widgets.Layout(width="140px")
)

# Date of 100th Case Date Picker
custom_date_widget = widgets.DatePicker(
    value=datetime.date(2020, 3, 1),
    description="100th Case",
    disabled=False,
)

# Custom Label Text Box
custom_text_label_widget = widgets.Text(
    placeholder='City, State, Country',
    description='Custom Title',
    disabled=False
)

# Custom Scenario "Plot Data" Button
custom_plot_data_btn = widgets.Button(
    description="Plot Data",
    disabled=False,
    layout=widgets.Layout(margin="0 0 0 93px")
)

# First Row Horizontal Box
custom_row1 = widgets.HBox([
    number_of_days_widget, 
    population_widget, widgets.Label(value="Million"),
])

# Second Row Horizontal Box
custom_row2 = widgets.HBox([
    custom_date_widget, 
    rnaught_slider,
])

# Third Row Horizontal box
custom_row3 = widgets.HBox([
    custom_text_label_widget,
    percent_of_population_infected
])

# Entire Custom Scenario User Inputs
custom_input_widgets = widgets.VBox([
    custom_row1,
    custom_row2,
    custom_row3,
    custom_plot_data_btn
])

#####################################################
# Tabs
tab_contents = [
    "Entity Projections",
    "Full SIR Model", 
    # "Multiple Entities", 
    # "Social Distancing",
    "Social Distancing",
    "Custom Scenario"
]

# Widgets/User Interfaces in the tabs
children = [
    multiple_rnaught_input_widgets,
    single_entity_input_widgets, 
    # multiple_entity_input_widgets,
    # multiple_f_widgets,
    relax_sd_widgets,
    custom_input_widgets,
]

# Create tab widget
user_input_tabs = widgets.Tab()
user_input_tabs.children = children
for i in range(len(tab_contents)):
    user_input_tabs.set_title(i, tab_contents[i])

# Display tabs and output area
display(user_input_tabs)
display(out)


# Event Handlers: Plot Data buttons
single_entity_plot_data_btn.on_click(sir_plot_one_entity)
multiple_entity_plot_data_btn.on_click(plot_multiple_entities)
multiple_rnaught_plot_data_btn.on_click(plot_multiple_rnaughts)
multiple_f_plot_data_btn.on_click(plot_multiple_f_values)
# damping_f_plot_data_btn.on_click(plot_damping_f)
relax_sd_plot_data_btn.on_click(relax_social_distancing)
custom_plot_data_btn.on_click(plot_custom_data)

# Event Handler: Best Fit Button
best_fit_btn.on_click(set_best_fit_parameters)

# Event Handler: CSV Buttons
clear_csv_btn.on_click(clear_csv_file)
add_to_csv_btn.on_click(add_to_csv_file)

# Event Handlers: Dropdown Menus and Selectors
multiple_entity_type_selector.observe(multiple_entity_type_change)
country_selector.observe(load_states)
state_selector.observe(load_cities)
city_selector.observe(city_data)

Output(layout=Layout(height='450px'))